In [1]:
import os
import numpy as np
import scipy as sp
from scipy.stats import pearsonr, spearmanr
from sklearn.ensemble import RandomForestRegressor, RandomForestClassifier
from sklearn.grid_search import GridSearchCV
from sklearn.metrics import mean_squared_error, classification_report, precision_recall_fscore_support
import sys
import matplotlib.pyplot as plt
import random
import difflib

from sklearn.pipeline import make_pipeline
from sklearn import preprocessing
from sklearn import linear_model
from sklearn.feature_selection import SelectFromModel
from sklearn.externals import joblib
import re
import argparse


/Users/yanakahitomi/.pyenv/versions/3.5.0/envs/ccg2lambda/lib/python3.5/site-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)
/Users/yanakahitomi/.pyenv/versions/3.5.0/envs/ccg2lambda/lib/python3.5/site-packages/sklearn/grid_search.py:43: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. This module will be removed in 0.20.
  DeprecationWarning)


In [17]:
def rmse(x, y):
    ## x:targets y:predictions
    return ((y - x) ** 2).mean(axis=0)

In [4]:
with open('./features_np_again.pickle', 'rb') as in_f:
    train_sources = np.load(in_f)
    train_targets = np.load(in_f)
    trial_sources = np.load(in_f)
    trial_tragets = np.load(in_f)
    train_id = np.load(in_f)
    trial_id = np.load(in_f)


In [7]:
np.set_printoptions(threshold=np.inf)
train_sources

array([[  0.00000000e+00,   0.00000000e+00,   1.00000000e+00,
          1.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          5.00000000e-01,   5.00000000e-01,   0.00000000e+00,
          5.00000000e-01,   5.00000000e-01,   5.00000000e+00,
          0.00000000e+00,   5.00000000e+00,   2.00000000e+01,
          2.50000000e-01,   5.50000000e-01,   0.00000000e+00,
          0.00000000e+00,   0.00000000e+00,   1.00000000e-01,
          1.00000000e-01,   2.90000000e+01,   0.00000000e+00,
          0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          3.79310345e-01,   3.10344828e-01,   3.10344828e-01,
          0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          0.00000000e+00,   2.00000000e-01,   0.00000000e+00,
          0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          0.00000000e+00,   2.00000000e-01,   0.00000000e+00,
          0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
          0.00000000e+00,   0.00000000e+00,   0.00000000e+00,
        

In [14]:
from sklearn.metrics import mean_squared_error, classification_report, accuracy_score, f1_score

In [2]:
f = open("all_result_rte.txt", "r")
lines = f.readlines()
f.close()
#0: unk, 1: no, 2: yes
preds = [line.split()[1] for line in lines]
preds_yn = [pred for pred in preds if pred == "1" or pred == "2"]
preds_unk = [pred for pred in preds if pred == "0"]
corrs = [line.split()[2] for line in lines]
corrs_yn = [line.split()[2] for line in lines]
corrs_yn = [line.split()[2] for line in lines]

In [3]:
import pandas as pd

In [73]:
#tb.loc[:, "entailment_judgment"]
#tb.loc[:, "correct_answer"]
import pandas as pd
tb = pd.read_table("results_20170921_WN/ablsteps_all_result_rte.txt", header=0)
tp = len(tb.query('entailment_judgment == 1&entailment_judgment == correct_answer|entailment_judgment == 2&entailment_judgment == correct_answer'))
tpfp =  len(tb.query('entailment_judgment == 1|entailment_judgment == 2')) 
prec = float(tp/tpfp)
tpfn =  len(tb.query('correct_answer == 1|correct_answer == 2')) 
rec = float(tp/tpfn)
corr = len(tb.query('entailment_judgment == correct_answer'))
acc = float(corr/len(tb))
print("{:.4f}, {:.4f}, {:.4f}".format(prec, rec, acc))

tp = len(tb.query('entailment_judgment == 1&entailment_judgment == correct_answer'))
tpfp =  len(tb.query('entailment_judgment == 1')) 
prec = float(tp/tpfp)
tpfn =  len(tb.query('correct_answer == 1')) 
rec = float(tp/tpfn)
corr = len(tb.query('entailment_judgment == correct_answer'))
acc = float(corr/len(tb))
print("{:.4f}, {:.4f}, {:.4f}".format(prec, rec, acc))

0.9176, 0.7345, 0.8569
0.9477, 0.7322, 0.8569


In [36]:
g = open("./ablation_new.txt", "r")
commands = g.readlines()
g.close()
for command in commands:
    train, trial = [], []
    command = command.strip()
    lines = command.split("\t")
    name = lines[0]
    if re.search("\,", lines[1]):
       	train = [i for i in re.split(r',',lines[1]) if i != '']
        trial = [i for i in re.split(r',',lines[2]) if i != '']
    tb = pd.read_table("./results_rebuttal/"+name+"all_result_rte.txt", header=0)
    tp = len(tb.query('entailment_judgment == 1|entailment_judgment == 2&entailment_judgment == correct_answer'))
    tpfp =  len(tb.query('entailment_judgment == 1|entailment_judgment == 2')) 
    prec = float(tp/tpfp)
    tpfn =  len(tb.query('correct_answer == 1|correct_answer == 2')) 
    rec = float(tp/tpfn)
    corr = len(tb.query('entailment_judgment == correct_answer'))
    acc = float(corr/len(tb))
    w = open("./results/"+name+"rte_new_result.txt")
    w.write("{%04.4f}, {%04.4f}, {%04.4f}".format(prec, rec, acc))
    w.close()

FileNotFoundError: File b'./results_w2v/isopredall_result_rte.txt' does not exist

In [14]:
def plot_deviation(outputs, actual, results):
    plt.figure(figsize=(12, 6))
    plt.subplot(1, 2, 1)
    plt.title('Comparison')

    zipped = sorted(zip(outputs, actual), key=lambda x: x[1])
    outputs = [i[0] for i in zipped]
    actual = [i[1] for i in zipped]


    plt.plot(np.arange(len(outputs)) + 1, outputs, 'b.', 
        label='Predicted values')
    plt.plot(np.arange(len(outputs)) + 1, actual, 'r-', 
        label='Actual values')

    plt.legend(loc='upper left')
    plt.xlabel('Sentence no.')
    plt.ylabel('Relatedness')

    plt.savefig('./'+results+'/result.png', bbox_inches='tight')


In [19]:
with open('./features_np_again.pickle', 'rb') as in_f:
    train_sources = np.load(in_f)
    #tree train_sources2 = train_sources[:, 69:70]
    train_sources2 = train_sources[:, 70:71]
    train_targets = np.load(in_f)
    trial_sources = np.load(in_f)
    #tree trial_sources2 = trial_sources[:, 69:70]
    trial_sources2 = trial_sources[:, 70:71]
    trial_targets = np.load(in_f)
    train_id = np.load(in_f)
    trial_id = np.load(in_f)

# Train the regressor
#clf = joblib.load('results_rebuttal/isotree_randomforestregressor.pkl')
clf = joblib.load('results_rebuttal/isopassive_randomforestregressor.pkl')

# Apply regressor to trial data
outputs = clf.predict(trial_sources2)
plot_deviation(outputs, trial_targets, "results_rebuttal")

In [20]:
rmse(outputs, trial_targets)

1.0092826366080205